In [1]:
import pandas as pd
import numpy as np
import re
import spacy

#Example train_data
TRAINING_DATA = [
    ("How to preorder the iPhone X", {'entities': [(20, 28, 'GADGET')]})

# Create entities with multiple categories

In [2]:
categories = {'CHARACTERS': ['character','Arthur Fleck', 'Arthur', 'Murray Franklin','Sophie Dumond','Penny Fleck'],
 'TALENT': ['actor','actress','talent','director','Joaquin Phoenix','Robert De Niro','Zazie Beetz','Frances Conroy','Todd Philips'],
 'PLOT': ['plot', 'frame', 'scene', 'story', 'stories'],
 'TICKETS': ['ticket', 'presale'],
 'SOUNDTRACK': ['music', 'song'],
 'SPECIAL EFFECTS': ['FX', 'visual effects', 'graphics', 'postproduction'],
 'COSTUME DESIGN': ['costum', 'costume designer'],
 'HYPE': ['hype','hyyyype','amazing','awesome','desire','premiere','Cant wait'],
 'BOX OFFICE': ['box office'],
 'REVIEWS': ['review'],
 'TRAILER': ['trailer']}

In [3]:
df = pd.read_csv('../input/#jokermovie.csv')
dfText = df[['id', 'text']]
dfText.head()

id                                               text
0  1180633752885743616  People at the cinema thinking they got the #Jo...
1  1180633751744913408  I have a new favorite joker @jokermovie #Joker...
2  1180633723932483584  ⭐⭐⭐⭐⭐ Performance, what a movie #JokerMovie pi...
3  1180633642198077441  #JokerMovie was absolutely amazing and ended w...
4  1180633577693880321  I just want to give both Arthur Fleck and Gary...

In [4]:
#Get dictionary reversed
def invertDict(dictionary):
    new_categories = dict()

    for category, lista in categories.items():
        for word in lista:
            new_categories.update({word:category})
        
    return new_categories

In [5]:
newdictionary = invertDict(categories)
newdictionary

{'character': 'CHARACTERS',
 'Arthur Fleck': 'CHARACTERS',
 'Arthur': 'CHARACTERS',
 'Murray Franklin': 'CHARACTERS',
 'Sophie Dumond': 'CHARACTERS',
 'Penny Fleck': 'CHARACTERS',
 'actor': 'TALENT',
 'actress': 'TALENT',
 'talent': 'TALENT',
 'director': 'TALENT',
 'Joaquin Phoenix': 'TALENT',
 'Robert De Niro': 'TALENT',
 'Zazie Beetz': 'TALENT',
 'Frances Conroy': 'TALENT',
 'Todd Philips': 'TALENT',
 'plot': 'PLOT',
 'frame': 'PLOT',
 'scene': 'PLOT',
 'story': 'PLOT',
 'stories': 'PLOT',
 'ticket': 'TICKETS',
 'presale': 'TICKETS',
 'music': 'SOUNDTRACK',
 'song': 'SOUNDTRACK',
 'FX': 'SPECIAL EFFECTS',
 'visual effects': 'SPECIAL EFFECTS',
 'graphics': 'SPECIAL EFFECTS',
 'postproduction': 'SPECIAL EFFECTS',
 'costum': 'COSTUME DESIGN',
 'costume designer': 'COSTUME DESIGN',
 'hype': 'HYPE',
 'hyyyype': 'HYPE',
 'amazing': 'HYPE',
 'awesome': 'HYPE',
 'desire': 'HYPE',
 'premiere': 'HYPE',
 'Cant wait': 'HYPE',
 'box office': 'BOX OFFICE',
 'review': 'REVIEWS',
 'trailer': 'TRAIL

In [6]:
def localize(pattern, text):
    #Localize where the pattern match the text
    x = re.search(pattern, text).span()
    return x

In [7]:
#Return a list of tuples: word matching and topic
def findCategory(publication, reverseddict):
    sentence = re.findall('\w+', publication)

    category = []
    for word in sentence:
        topic = reverseddict.get(word, None)
        if topic:
            category.append((word,topic))

    return category

In [8]:
#Create entity for the training data: text + dictionary with entities
def entity(text, reverseddictionary):
    matcher = findCategory(text, newdictionary)
    if matcher != '':
    
        tupla = []
        #Locate word matching and create a tuple 
        for i in range(len(matcher)):
            localizer = localize(matcher[i][0], text)
            group = []
            group.append(localizer[0]), group.append(localizer[1]), group.append(matcher[i][1])
            tupla.append(tuple(group))

        entity = dict()
        entity.update({'entities': tupla})
        data = [text, entity]
        return data
    else:
        return (
        text,
        {"entities": []},)


# Create a training data with 300 samples

In [9]:
#New DataFrame with just 300 samples
dfText300 = dfText[:301]

In [10]:
#Create training data iterating over the DataFrame and applying entity function
training_data = []
for i in dfText300['text'].tolist():
    training_data.append(entity(i, newdictionary))

training_data

[['People at the cinema thinking they got the #JokerMovie  plot like: pic.twitter.com/FULbcu3SBj',
  {'entities': [(56, 60, 'PLOT')]}],
 ['I have a new favorite joker @jokermovie #JokerMovie pic.twitter.com/S4wOE3lmQF',
  {'entities': []}],
 ['⭐⭐⭐⭐⭐ Performance, what a movie #JokerMovie pic.twitter.com/vGun5i7WPW',
  {'entities': []}],
 ["#JokerMovie was absolutely amazing and ended with a BANG!!! \n\nA must watch if you're a comic book fan. \n#Joker #MustWatchpic.twitter.com/idTvidHpbE",
  {'entities': [(27, 34, 'HYPE')]}],
 ['I just want to give both Arthur Fleck and Gary a hug. #JokerMovie #Joker #JokerFilm',
  {'entities': [(25, 31, 'CHARACTERS')]}],
 ['These 3 actors BETTER get nominated or even win an Oscar. #AvengersEndgame #JokerMovie #ITChapterTwopic.twitter.com/Sd9Ele81wz',
  {'entities': []}],
 ['To me the revelation of #JokerMovie is Todd Philips who we all know for making comedies like Hangover. There are obvious tributes to Scorsese but this is very dark, unsettling and t

# Create an English blank model to train

In [11]:
from __future__ import unicode_literals, print_function

import plac
import random
from pathlib import Path
import spacy
from spacy.util import minibatch, compounding





@plac.annotations(
    model=("Model name. Defaults to blank 'en' model.", "option", "m", str),
    output_dir=("Optional output directory", "option", "o", Path),
    n_iter=("Number of training iterations", "option", "n", int),
)
def main(TRAIN_DATA, model=None, output_dir=None, n_iter=100):
    """Load the model, set up the pipeline and train the entity recognizer."""
    if model is not None:
        nlp = spacy.load(model)  # load existing spaCy model
        print("Loaded model '%s'" % model)
    else:
        nlp = spacy.blank("en")  # create blank Language class
        print("Created blank 'en' model")

    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if "ner" not in nlp.pipe_names:
        ner = nlp.create_pipe("ner")
        nlp.add_pipe(ner, last=True)
    # otherwise, get it so we can add labels
    else:
        ner = nlp.get_pipe("ner")

    # add labels
    for _, annotations in TRAIN_DATA:
        for ent in annotations.get("entities"):
            ner.add_label(ent[2])

    # get names of other pipes to disable them during training
    pipe_exceptions = ["ner", "trf_wordpiecer", "trf_tok2vec"]
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe not in pipe_exceptions]
    with nlp.disable_pipes(*other_pipes):  # only train NER
        # reset and initialize the weights randomly – but only if we're
        # training a new model
        if model is None:
            nlp.begin_training()
        for itn in range(n_iter):
            random.shuffle(TRAIN_DATA)
            losses = {}
            # batch up the examples using spaCy's minibatch
            batches = minibatch(TRAIN_DATA, size=compounding(4.0, 32.0, 1.001))
            for batch in batches:
                texts, annotations = zip(*batch)
                nlp.update(
                    texts,  # batch of texts
                    annotations,  # batch of annotations
                    drop=0.5,  # dropout - make it harder to memorise data
                    losses=losses,
                )
            print("Losses", losses)

    # test the trained model
    for text, _ in TRAIN_DATA:
        doc = nlp(text)
        print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
        print("Tokens", [(t.text, t.ent_type_, t.ent_iob) for t in doc])

    # save model to output directory
    if output_dir is not None:
        output_dir = Path(output_dir)
        if not output_dir.exists():
            output_dir.mkdir()
        nlp.to_disk(output_dir)
        print("Saved model to", output_dir)

        # test the saved model
        print("Loading from", output_dir)
        nlp2 = spacy.load(output_dir)
        for text, _ in TRAIN_DATA:
            doc = nlp2(text)
            print("Entities", [(ent.text, ent.label_) for ent in doc.ents])
            print("Tokens", [(t.text, t.ent_type_, t.ent_iob) for t in doc])


if __name__ == "__main__":
    pass

In [12]:
main(training_data, None, '../output/modelgraphext', 100)

Created blank 'en' model
Losses {'ner': 916.2171370221122}
Losses {'ner': 103.94928340406258}
Losses {'ner': 115.24384189608857}
Losses {'ner': 104.46839462674711}
Losses {'ner': 86.66839831347133}
Losses {'ner': 77.82290434783428}
Losses {'ner': 61.78477577464718}
Losses {'ner': 62.555713807011145}
Losses {'ner': 59.68888383858958}
Losses {'ner': 45.463184695687886}
Losses {'ner': 41.15330617324822}
Losses {'ner': 38.74991051867195}
Losses {'ner': 35.43542599899971}
Losses {'ner': 36.17898792982385}
Losses {'ner': 23.814971295944105}
Losses {'ner': 20.404880924221317}
Losses {'ner': 23.521748911107302}
Losses {'ner': 21.794524582640324}
Losses {'ner': 19.77812066261073}
Losses {'ner': 10.395516644786158}
Losses {'ner': 14.846057764787416}
Losses {'ner': 9.331299538590356}
Losses {'ner': 9.951953717979338}
Losses {'ner': 12.965056289925581}
Losses {'ner': 9.181927787789032}
Losses {'ner': 10.288356725300607}
Losses {'ner': 11.469186506139936}
Losses {'ner': 4.973036277348427}
Losses {'

Entities []
Tokens [('It', '', 2), ("'s", '', 2), ('not', '', 2), ('released', '', 2), ('in', '', 2), ('my', '', 2), ('city', '', 2), (',', '', 2), (' ', '', 2), ('so', '', 2), ('unlucky', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('😭', '', 2), ('😭', '', 2)]
Entities []
Tokens [('Rey', '', 2), ('@bookmyshow', '', 2), ('tickets', '', 2), ('open', '', 2), ('cheyyu', '', 2), ('ra', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('vi', '', 2), ('Hyd', '', 2), ('lo', '', 2), ('😡', '', 2), ('😡', '', 2), ('😡', '', 2), ('\n', '', 2), ('#', '', 2), ('Joker', '', 2)]
Entities []
Tokens [('Looking', '', 2), ('for', '', 2), ('a', '', 2), ('win', '', 2), ('.', '', 2), ('Put', '', 2), ('in', '', 2), ('the', '', 2), ('work', '', 2), ('.', '', 2), ('Earn', '', 2), ('the', '', 2), ('W.', '', 2), ('#', '', 2), ('TuesdayThoughts', '', 2), ('#', '', 2), ('TuesdayMorning', '', 2), ('#', '', 2), ('TuesdayMotivation', '', 2), ('#', '', 2), ('tuesdayvibes', '', 2), ('#', '', 2), ('TuesdayTrivia', '', 2), ('#

Entities []
Tokens [('@YellowFlashGuy', '', 2), ('reacts', '', 2), ('to', '', 2), ('the', '', 2), ('news', '', 2), ('about', '', 2), ('#', '', 2), ('WarnerBros', '', 2), ("'", '', 2), ('decision', '', 2), ('to', '', 2), ('ban', '', 2), ('everyone', '', 2), ('(', '', 2), ('except', '', 2), ('photographers', '', 2), (')', '', 2), ('of', '', 2), ('the', '', 2), ('press', '', 2), ('from', '', 2), ('appearing', '', 2), ('at', '', 2), ('the', '', 2), ('#', '', 2), ('RedCarpet', '', 2), ('screening', '', 2), ('of', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('.', '', 2), ('https://youtu.be/mD7TWIC1N8c', '', 2), ('\xa0 ', '', 2), ('via', '', 2), ('@YouTube', '', 2)]
Entities [('Arthur', 'CHARACTERS')]
Tokens [('Predicting', '', 2), ('Arthur', 'CHARACTERS', 3), ('Fleck', '', 2), ('"', '', 2), ('Joker', '', 2), ('"', '', 2), ('2017', '', 2), ('haahha', '', 2), ('.', '', 2), ('\n', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('pic.twitter.com/9eAeZOeY2j', '', 2)]
Entities []
Tokens [('Joker', 

Entities []
Tokens [('I', '', 2), ('ca', '', 2), ("n't", '', 2), ('wait', '', 2), ('for', '', 2), ('date', '', 2), ('night', '', 2), ('!', '', 2), ('!', '', 2), ('!', '', 2), ('!', '', 2), ('!', '', 2), ('!', '', 2), ('!', '', 2), ('Thanks', '', 2), ('@ree.la_07', '', 2), ('Queen', '', 2), ('Booboo', '', 2), ('!', '', 2), ('!', '', 2), ('\n', '', 2), ('#', '', 2), ('HealthisWealth', '', 2), ('#', '', 2), ('PleasureIsTreasure', '', 2), ('#', '', 2), ('jokermovie', '', 2), ('\n', '', 2), ('#', '', 2), ('PureHappiness', '', 2), (' ', '', 2), ('#', '', 2), ('DangDang', '', 2), ('\n', '', 2), ('#', '', 2), ('NewLight', '', 2), (' ', '', 2), ('#', '', 2), ('Blessed', '', 2), ('#', '', 2), ('Dointhemost', '', 2), ('#', '', 2), ('TeamBooBoo', '', 2), ('#', '', 2), ('BestLife', '', 2), ('#', '', 2), ('positivevibes', '', 2), ('#', '', 2), ('Soberlife', '', 2), ('#', '', 2), ('ReeLa', '', 2), ('#', '', 2), ('relationshipgoals', '', 2), ('https://ift.tt/2nXHEW6', '', 2), ('\xa0', '', 2), ('pic.tw

Entities []
Tokens [('You', '', 2), ('think', '', 2), ('when', '', 2), ('someone', '', 2), ('bumps', '', 2), ('into', '', 2), ('Joaquin', '', 2), ('Phoenix', '', 2), ('he', '', 2), ('shouts', '', 2), ('“', '', 2), ('Hey', '', 2), ('!', '', 2), ('I', '', 2), ('’m', '', 2), ('Joaquin', '', 2), ('here', '', 2), ('!', '', 2), ('”', '', 2), ('#', '', 2), ('JokerMovie', '', 2)]
Entities []
Tokens [('#', '', 2), ('JokerMovie', '', 2), ('A', '', 2), ('thread', '', 2), ('.', '', 2), ('This', '', 2), ('film', '', 2), ('has', '', 2), ('left', '', 2), ('me', '', 2), ('with', '', 2), ('lingering', '', 2), (',', '', 2), ('startling', '', 2), ('images', '', 2), ('24', '', 2), ('hours', '', 2), ('after', '', 2), ('seeing', '', 2), ('it', '', 2), ('.', '', 2), ('Yes', '', 2), (',', '', 2), ('Joaquin', '', 2), ('Phoenix', '', 2), ('can', '', 2), ('take', '', 2), ('the', '', 2), ('bloody', '', 2), ('joker', '', 2), ('crown', '', 2), ('.', '', 2), ('But', '', 2), ('...', '', 2), ('pic.twitter.com/T5MaDZwU

...

Entities []
Tokens [('Fan', '', 2), ('art', '', 2), ('inspired', '', 2), ('by', '', 2), ('@jokermovie', '', 2), ('.', '', 2), ('I', '', 2), ('was', '', 2), ('having', '', 2), ('some', '', 2), ('"', '', 2), ('colada', '', 2), ('morada', '', 2), ('"', '', 2), ('and', '', 2), ('decided', '', 2), ('to', '', 2), ('play', '', 2), ('around', '', 2), ('with', '', 2), ('it', '', 2), ('...', '', 2), ('hope', '', 2), ('you', '', 2), ('like', '', 2), ('it', '', 2), ('!', '', 2), ('\n\n', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('\n', '', 2), ('#', '', 2), ('FanArt', '', 2), ('\n', '', 2), ('#', '', 2), ('ColadaMorada', '', 2), ('\n', '', 2), ('#', '', 2), ('WarnerBros', '', 2), ('\n', '', 2), ('#', '', 2), ('DCComics', '', 2), ('\n', '', 2), ('#', '', 2), ('Joker', '', 2), ('\n', '', 2), ('#', '', 2), ('Batmanpic.twitter.com', '', 2), ('/', '', 2), ('C1mT62oZLB', '', 2)]
Entities []
Tokens [('Who', '', 2), ('wanna', '', 2), ('go', '', 2), ('see', '', 2), ('the', '', 2), ('Joker', '', 2), ('mo

Entities [('story', 'PLOT')]
Tokens [('#', '', 2), ('JokerMovie', '', 2), ('Add', '', 2), ('it', '', 2), ('is', '', 2), ('#', '', 2), ('Jokerit', '', 2), ('another', '', 2), ('#', '', 2), ('clownstar', '', 2), (' ', '', 2), ('horror', '', 2), ('story', 'PLOT', 3), ('or', '', 2), ('#', '', 2), ('shooting', '', 2), ('tales', '', 2), ('by', '', 2), ('some', '', 2), ('guilty', '', 2), ('criminal', '', 2), ('guys', '', 2), ('!', '', 2)]
Entities []
Tokens [('I', '', 2), ('’m', '', 2), ('going', '', 2), ('to', '', 2), ('see', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('tomorrow', '', 2), ('after', '', 2), ('work', '', 2), ('since', '', 2), ('I', '', 2), ('have', '', 2), ('to', '', 2), ('stay', '', 2), ('at', '', 2), ('the', '', 2), ('theatre', '', 2), ('later', '', 2), ('when', '', 2), ('I', '', 2), ('get', '', 2), ('off', '', 2), ('and', '', 2), ('there', '', 2), ('’s', '', 2), ('nothing', '', 2), ('else', '', 2), ('showing', '', 2), ('around', '', 2), ('the', '', 2), ('time', '', 2), ('

Entities []
Tokens [('In', '', 2), ('theaters', '', 2), ('this', '', 2), ('Thursday', '', 2), ('.', '', 2), ('Get', '', 2), ('tickets', '', 2), (':', '', 2), ('http://Fandango.com', '', 2), ('/', '', 2), ('JokerMovie', '', 2), ('\xa0 ', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('pic.twitter.com/owbk6Y0gpQ', '', 2)]
Entities []
Tokens [('So', '', 2), (',', '', 2), ('why', '', 2), ('is', '', 2), ('people', '', 2), ('complaining', '', 2), ('about', '', 2), ('the', '', 2), ('#', '', 2), ('JokerMovie', '', 2)]
Entities [('awesome', 'HYPE')]
Tokens [('#', '', 2), ('JokerMovie', '', 2), ('was', '', 2), ('awesome', 'HYPE', 3), ('.', '', 2), (' ', '', 2), ('A', '', 2), ('great', '', 2), ('blackpill', '', 2), ('Movie', '', 2), ('.', '', 2), (' ', '', 2), ('10', '', 2), ('out', '', 2), ('of', '', 2), ('10', '', 2), ('for', '', 2), ('me', '', 2), ('.', '', 2)]
Entities []
Tokens [('After', '', 2), ('seeing', '', 2), ('this', '', 2), ('I', '', 2), ('really', '', 2), ('urge', '', 2), ('people', 

Entities []
Tokens [('#', '', 2), ('BigMouth', '', 2), ('Season', '', 2), ('3', '', 2), ('comes', '', 2), ('out', '', 2), ('on', '', 2), ('Friday', '', 2), ('and', '', 2), ('so', '', 2), ('does', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('what', '', 2), ('one', '', 2), ('do', '', 2), ('I', '', 2), ('watch', '', 2), ('first', '', 2), ('and', '', 2), ('how', '', 2), ('do', '', 2), ('I', '', 2), ('cancel', '', 2), ('all', '', 2), ('my', '', 2), ('weekend', '', 2), ('plans', '', 2), ('?', '', 2), ('!', '', 2), ('#', '', 2), ('Adulting', '', 2)]
Entities []
Tokens [('Put', '', 2), ('on', '', 2), ('a', '', 2), ('happy', '', 2), ('face', '', 2), ('\n\n', '', 2), ('@jokermovie', '', 2), ('\n\n', '', 2), ('#', '', 2), ('Joker', '', 2), ('#', '', 2), ('JokerMovie', '', 2), ('#', '', 2), ('JoaquinPhoenixpic.twitter.com', '', 2), ('/', '', 2), ('F6qjoDAVrf', '', 2)]
Entities []
Tokens [('"', '', 2), ('Joaquin', '', 2), ('Phoenix', '', 2), ("'s", '', 2), ('performance', '', 2), ('is', '', 2), (

Entities [('Arthur', 'CHARACTERS')]
Tokens [('PS', '', 2), (')', '', 2), ('#', '', 2), ('PlotTwist', '', 2), (',', '', 2), ('Arthur', 'CHARACTERS', 3), ('"', '', 2), ('Happy', '', 2), ('"', '', 2), ('Fleck', '', 2), ('is', '', 2), ('the', '', 2), ('bridge', '', 2), ('between', '', 2), ('#', '', 2), ('Marvel', '', 2), ('and', '', 2), ('#', '', 2), ('DC', '', 2), (',', '', 2), ('as', '', 2), ('he', '', 2), ('later', '', 2), ('becomes', '', 2), ('#', '', 2), ('TonyStark', '', 2), ("'s", '', 2), ('bodyguard', '', 2), ('.', '', 2), ('#', '', 2), ('JokerMovie', '', 2)]
Entities []
Tokens [('All', '', 2), ('right', '', 2), ('society', '', 2), (',', '', 2), ('let', '', 2), ('me', '', 2), ('live', '', 2), ('in', '', 2), ('you', '', 2), ('.', '', 2), ('#', '', 2), ('jokermovie', '', 2), ('jokermovie', '', 2), ('@', '', 2), ('AMC', '', 2), ('River', '', 2), ('East', '', 2), (',', '', 2), ('Chicago', '', 2), ('https://www.instagram.com/p/B3GCxq3p_YO/?igshid=liz00n5kbjvq', '', 2), ('\xa0', '', 2), 

In [16]:
nlp = spacy.load('../output/modelgraphext')

for index, row in dfText.iterrows():
    doc = nlp(row['text'])
    print(doc)
    print(ent)
    for ent in doc.ents:
        dfText.loc[index, 'category'] = [(ent.label_)]
        print([(ent.label_)])
#dfText.to_csv('../output/graphextpredicted.csv')

People at the cinema thinking they got the #JokerMovie  plot like: pic.twitter.com/FULbcu3SBj
character
['PLOT']
I have a new favorite joker @jokermovie #JokerMovie pic.twitter.com/S4wOE3lmQF
plot
⭐⭐⭐⭐⭐ Performance, what a movie #JokerMovie pic.twitter.com/vGun5i7WPW
plot
#JokerMovie was absolutely amazing and ended with a BANG!!! 

A must watch if you're a comic book fan. 
#Joker #MustWatchpic.twitter.com/idTvidHpbE
plot
['HYPE']
I just want to give both Arthur Fleck and Gary a hug. #JokerMovie #Joker #JokerFilm
amazing
['CHARACTERS']
These 3 actors BETTER get nominated or even win an Oscar. #AvengersEndgame #JokerMovie #ITChapterTwopic.twitter.com/Sd9Ele81wz
Arthur
To me the revelation of #JokerMovie is Todd Philips who we all know for making comedies like Hangover. There are obvious tributes to Scorsese but this is very dark, unsettling and tight- I can’t really think of any parts where film dragged
Arthur
And the Oscar goes to ... #JoaquinPhoenix!
Genius Performance 👏🏼👏🏼👏🏼👏🏼

#Joke

Hey clowns. Like IPAs? Snag a Trickster IPA from @GreenManBrewing at The Springs and get a free pint glass! See you this weekend for the #JokerMovie starring #JoaquinPhoenix. 🤡pic.twitter.com/3RU3u383BB
character
I cannot wait to watch #JokerMovie on saturday its gunna be so good 😁 pic.twitter.com/EYQhw5UBLd
character
put on a happy face #JokerMovie #Joker #JoaquinPhoenix #FilmTwitterpic.twitter.com/Naf779Hj8Y
character
If Joaquin Phoenix doesn't get an Oscar for his role in Joker, then the film industry haven't a clue what outstanding acting is. #Joker #JokerMovie #JoaquinPhoenix
character
So three awesome movies are coming out soon which I cannot wait for. #ElCaminoABreakingBadMovie, #Joker #JokerMovie & #TerminatorDarkFate. 

Really looking forward to these movies.
character
['HYPE']
#jokermovie jokermovie #screening https://www.instagram.com/p/B3IopVlAZnA/?igshid=1on4hoohdvp4e …
awesome
I’m excited of this MASTERPIECE! #JokerMovie
awesome
Happy #JokerMovie release day
awesome
I’ve 

['CHARACTERS']
Wasn't really sure what to expect from #JokerMovie but the montage where he tries on all the different facepaint styles like Bozo, Emmett Kelly, and The Crow makeup was worth the price of the popcorn for sure. Plus you don't hear "All Star" on enough soundtracks these days.
character
Next Friday everybody be seeing the #JokerMovie while I’m seeing it on Thursday pic.twitter.com/OhwJSuFjSY
character
Arthur Fleck
-
#JokerMovie #Joker #dccomics #JoaquinPhoenixpic.twitter.com/OCBL4x6ppY
character
['CHARACTERS']
Hang on... #JokerMovie 
shouldn't exist? This movie is going be awful?
This is where I have to remind everyone that the views of some members of @SoWizardPodcast does not reflect the views & opinions of all the cohost.
Oh we might debating at #NYCC2019https://youtu.be/2ch_rn60BlU 
Arthur
Joker 🤡
-
#JokerMovie #Joker #dccomics #JoaquinPhoenixpic.twitter.com/YzpeC9uqDU
Arthur
“Joaquin Phoenix is astonishing.” Experience #JokerMovie on the state's largest screen beginnin

desire
Movie Review: #JokerMovie An uncomfortable, unoriginal approach but with a phenomenal performance behind it. https://youtu.be/zLKV8lj_kL4 
desire
If Joaquin Phoenix doesn't get an Oscar for his portrayal of the Joker I'm throw hands with @TheAcademy #JokerMovie pic.twitter.com/LNIgdVPzKu
desire
I should secretly go see #jokermovie alone because I deserve it.
desire
For beats(FREE) and mixing services come check out my store. NEW BEATS EVERY MONDAY

http://MarcelDM.Beatstars.com  

#MusicProducer #NewMusic #IndieArtist #BeatStars #JokerMovie #ThursdayThoughts
 #Instrumentals #TypeBeat #NationalBoyfriendDay #GrindSZN
desire
On my way to see #joker. Can't wait to see it.

Have read the snowflakes sites (@voxdotcom & @DEADLINE 2 name two)  scare tactics to keep ppl away. 

Its almost as if sites like these want something bad to happen, at a joker screening.  

 #joker2019   #jokermovie #rottentomatos
desire
Critics brigading RT with negative reviews because shooting didn't happen

#

['HYPE']
One of those moments that defined method acting. #TuesdayThoughts #TuesdayMorning #TuesdayMotivation #tuesdayvibes #TuesdayTrivia #TacoTuesday #October1st #October #October2019 #JokerMovie #Joker #JokerWeekhttps://twitter.com/RottenTomatoes/status/1179161316482863104 …
hype
Bold. Volcanic. Outstanding. #JokerMovie opens at #Cinergy Thursday night. Get advance tickets at https://cinergy.com/movie/joker/#tickets-anchor ….pic.twitter.com/9zf8ohj74C
hype
💚Mood because #jokermovie  comes out this Thursday. Does that make me crazy? Probably. jokermovie 💥 11/30 #30goingfor30challenge @ Downtown Long Beach https://www.instagram.com/p/B3GBKDgBCfP/?igshid=v78jujn9d9rd …
hype
Can’t not wait till Friday... #JokerMovie
hype
I can't wait for #JokerMovie this Friday. Tickets....check.
hype
#jokermovie what’s good @Wafflepops89
hype
Media stirs up everyone about the #JokerMovie 

Nothing happens

Media: Yeah well one guy was clapping and being loud so basically we were right!

https://www.bus

...

Guess who's excited to go see Joker tonight?????💚🤡💚🤡💚
#therearenowords 
.
.
.
#Joker #joaquinphoenix #jokermovie #toddphillips #soexcited #cantfuckingwait #losinmymind #arthurfleck #jokerlovers #greennails… https://www.instagram.com/p/B3PvyS0gYbN/?igshid=15s4dl1am0v7y …
review
#JokerMovie was INSANE
review
I wanna watch the #JokerMovie
review
So friggin’ intense. What a movie!!! #JokerMovie
review
So #JokerMovie is wildly good
review
#JokerMovie who wanna join me and we go cinema?? pic.twitter.com/qA8mJICTzR
review
Had a blast watching #JokerMovie with the #justusleague and then chilling  @DallasBBQ with @jodyscorner1 @ThaJay3Life @APiloto5 @uncannyshoe @Colts_All_Day88 and a bunch of dope subs!!!pic.twitter.com/nJaBVamVeY
review
The new Joker is the scariest thing I've ever seen in my entire life.

#JokerMovie pic.twitter.com/6yZEroQ3nu
review
After initially wanting to see the #JokerMovie two months ago I changed my mind because of the drama surrounding the movie. However Regal Crown

🎥🍣He's passionate about stand-up. Never mind that he's an awkward service-user; prone to inopportune laughter & violence. After Joker kills some bankers on the subway, the citizens of Gotham city rise up. And they're all wearing clown masks. pic.twitter.com/6TsQtx0lpb
character
The #JokerMovie was absolutely incredible. Brutal, violent and even funny at times. Joaquin Phoenix nails it, the score is phenomenal and the directing is top notch. I can definitely understand the controversy surrounding it; however, I feel the discussions that will accompany...
character
Watched #JokerMovie , it was a deep movie actually. Its worth it.
character
#JokerMovie was so beautifully shot and you can see the intentionality in every scene. That coupled with #JoaquinPhoenix playing the HELL out of that roll...it was hard to watch from an emotional stand point.
character
“Knock Knock” 

Jaw dropping performance by Joaquin Phoenix. Oscar is on the way..

#Joker #JokerMovie pic.twitter.com/P0bBevcUAz
chara

I'm definitely going to see #JokerMovie again. It's by far the most complex yet scintillating study of a character I've seen in years.

Remember this:
"Nobody is trying to understand anybody anymore."

Everyone has a story. All you gotta do is listen & it might save their lives. pic.twitter.com/dbWj8yrEpm
AMAZING
['CHARACTERS']
#JokerMovie is amazing, the way Joker character developed is so powerful you can feel his sadness & happiness.
character
['HYPE']
['CHARACTERS']
Going to see #JokerMovie today

Review Soon.....
character
#JokerMovie is on course to set second highest Indonesian OW in 2019 for 17+ rated movies (behind Hobbs & Shaw, $7M).

John Wick 3 was also (secretly) big, but I believe this one is bigger. More screens and whatnot. pic.twitter.com/Dz96jQCZTM
character
wow phew i saw #jokermovie trending and thought famed horologist Tom Jokermovie had died thank god pic.twitter.com/4JXH5Vdpzx
character
My friend’s review of the #JokerMovie  hahahahahahhhhhhhhhhh 😂😂 pic.twitter.c

#JokerMovie 10/10 .. WHAT A LEGENDARY PERFORMANCE BY JOAQUIN PHOENIX
amazing
#JokerMovie buddies please! 🤡
amazing
I thought this movie is a tragedy, but its a comedy. 🤡 #JokerMovie 9/10 Theres still hope for DC Movies pic.twitter.com/PwJxcrxPTe
amazing
It's Rowdy Network time...

Who is the Twitter handle in circle ??? 😜

Name you fav. handle that fits. 🔁

#SyeraaNarashimaReddy #SyeraNarasimhaReddy #RRR #Ntr #AlaVaikunthapurramuloo #War #JokerMovie pic.twitter.com/9VA4cPRnMS
amazing
It's probably irrational but
I'm not seeing #JokerMovie opening weekend for fear of terrorism.
amazing
Back from the #JokerMovie. And wow. You’ll know why Joker is the most popular comic book villain.
amazing
Ragam MASS #JokerMovie 2 Shows Added..😎😎 https://twitter.com/BreakingViews4u/status/1179751342966861824 …
amazing
LADIES AND GENTLEMEN, IT IS JOKER DAY #JokerMovie pic.twitter.com/HDDGoMpIxE
amazing
For the month of October in honor of #JokerMovie this is my new identity
amazing
Is the incel manlet so

First thing that is very clear after #JokerMovie is that Joaquin Phoenix deserves every award he is going to win.
story
There were some definite nods to Heath Ledger’s joker in #JokerMovie.  I actually don’t like stuff like that in a lot of movies, like a lot of Tarintino’s stuff are callbacks to other movies.  Still enjoyed it. Lots of good twist and turns as expected.  #multiplechoices
story
#JokerMovie is SOLD OUT at all Screening's at @blanchcentre @ODEONcinemasIRE Cinemas  there's loads of gone in to see it rite now I'll be going to see it tomorrow  I CAN NOT WAITE TO SEE IT  #JoaquinPhoenix IS A LEGEND
story
#JokerMovie starting in 10... 9... 8... 7... 6... 5... 4........
story
Slick want to go see 😈 #JokerMovie
story
*spoiler alert* When joker was like: "if it was me dying on the street you wouldn't notice me."  My thursty ass was like, "Honey boi, i'd notice u anywhere!" ;D XD #Joker #SpoilerAlert #Spoilers #JokerMovie #JokerFilm #joker2019 @ArthurFleck___
story
What are you go

In [19]:
dfText['category'].value_counts()

HYPE          1046
CHARACTERS     781
REVIEWS        369
TICKETS        216
PLOT           181
TALENT         157
TRAILER         31
SOUNDTRACK       9
Name: category, dtype: int64